In [29]:
%matplotlib inline
# Importing standard Qiskit libraries and configuring account
from qiskit import QuantumCircuit, execute, Aer, IBMQ
from qiskit import QuantumRegister, ClassicalRegister
from qiskit.compiler import transpile, assemble
from qiskit.tools.jupyter import *
from qiskit.visualization import *
from qiskit.circuit import Parameter
from qiskit.result import Result

#Q-CTRL Open Controls
from qctrlopencontrols import new_predefined_dds
#Q-CTRL Qiskit Adapter
from qctrlqiskit import convert_dds_to_qiskit_quantum_circuit
#Q-CTRL Visualizer
# from qctrlvisualizer import plot_sequences

import qiskit.ignis.verification.tomography as tom
from qiskit.providers.ibmq.managed import IBMQJobManager
from qiskit.providers.jobstatus import JOB_FINAL_STATES
from qiskit.quantum_info import state_fidelity
from qiskit.providers.aer import noise

# Importing other packages
import pickle
import numpy as np

# Import measurement calibration functions
from qiskit.ignis.mitigation.measurement import (complete_meas_cal, tensored_meas_cal,
                                                 CompleteMeasFitter, TensoredMeasFitter)
from itertools import product

# Loading your IBM Q account(s)
provider = IBMQ.load_account()

ibmqfactory.load_account:WARNING:2020-05-08 13:02:55,707: Credentials are already in use. The existing account in the session will be replaced.


In [2]:
%qiskit_job_watcher

Accordion(children=(VBox(layout=Layout(max_width='710px', min_width='710px')),), layout=Layout(max_height='500…

<IPython.core.display.Javascript object>

In [3]:
%qiskit_progress_bar
from qiskit.tools.parallel import parallel_map
parallel_map(np.sin, np.linspace(0,10,100));

In [4]:
from copy import deepcopy

In [5]:
#print('\n'.join([str(x) for x in provider.backends()]))
#print('---')
#print('\n'.join([str(x) for x in Aer.backends()]))
backend=provider.get_backend('ibmq_16_melbourne')
backend_sim=provider.get_backend('ibmq_qasm_simulator')
backend_sim_local=Aer.get_backend('qasm_simulator')
backend_sv=Aer.get_backend('statevector_simulator')

In [6]:
data_list=[0,1,2,3,4]
syn=[5]
flag=[6]

In [7]:
def StatePreparation(stabilizer=0):
    q = QuantumRegister(7)
    qc = QuantumCircuit(q)
    #prepare the 5-qubit graph state
    qc.h(q[0])
    qc.h(q[1])
    qc.h(q[2])
    qc.h(q[3])
    qc.h(q[4])
    qc.cz(q[0],q[1])
    qc.cz(q[2],q[3])
    qc.cz(q[1],q[2])
    qc.cz(q[3],q[4])
    qc.cz(q[0],q[4])
    #syndrome and flag extraction
    #stabilizer order: from left to right, Fig 2(a), SM of two extra qubits
    if(stabilizer==0):
        #first stabilizer 
        qc.h(q[5])
        qc.cx(q[5],q[0])
        qc.cx(q[5],q[6])
        qc.cz(q[1],q[5])
        qc.cx(q[5],q[6])
        qc.cz(q[4],q[5])
        qc.h(q[5])
    elif(stabilizer==1):
    #second stabilizer
        qc.h(q[5])
        qc.cz(q[0],q[5])
        qc.cx(q[5],q[6])
        qc.cx(q[5],q[1])
        qc.cx(q[5],q[6])
        qc.cz(q[2],q[5])
        qc.h(q[5])
    elif(stabilizer==2):
        #third stabilizer
        qc.h(q[5])
        qc.cx(q[5],q[3])
        qc.cx(q[5],q[6])
        qc.cz(q[2],q[5])
        qc.cx(q[5],q[6])
        qc.cz(q[4],q[5])
        qc.h(q[5])
    #measure syndrome and flag & do state tomography for the data qubits
    qc.barrier()
    #qc.measure(q[5],c[5])
    #qc.measure(q[6],c[6])
    return q, qc

In [8]:
q, qc=StatePreparation(0)
# ca = ClassicalRegister(1)
# qc.add_register(ca)
# qc.measure(q[0],ca[0])
qc.draw()
# qc.data

┌───┐         ┌───┐                      ░ 
q0_0: ┤ H ├─■─────■─┤ X ├──────────────────────░─
      ├───┤ │     │ └─┬─┘                      ░ 
q0_1: ┤ H ├─■──■──┼───┼────────■───────────────░─
      ├───┤    │  │   │        │               ░ 
q0_2: ┤ H ├─■──■──┼───┼────────┼───────────────░─
      ├───┤ │     │   │        │               ░ 
q0_3: ┤ H ├─■──■──┼───┼────────┼───────────────░─
      ├───┤    │  │   │        │               ░ 
q0_4: ┤ H ├────■──■───┼────────┼───────■───────░─
      ├───┤           │        │       │ ┌───┐ ░ 
q0_5: ┤ H ├───────────■────■───■───■───■─┤ H ├─░─
      └───┘              ┌─┴─┐   ┌─┴─┐   └───┘ ░ 
q0_6: ───────────────────┤ X ├───┤ X ├─────────░─
                         └───┘   └───┘         ░

To keep the consistence, the following blocks are mainly from `test state prep.ipynb`

In [9]:
import time

Based on https://github.com/Qiskit/qiskit-tutorials/blob/master/legacy_tutorials/ignis/6a_state_tomography.ipynb?fbclid=IwAR1Pf1nH2CBPUWDdsa_xBiYs1kYDu8hwI9dVvr63z7ypmhy2UlR6QpMgJWc, 2-Qubit Conditional State Tomography

we should have projected the ideal final state to the final state, 'reduced(v,sf)' returns the projected states based on 'sf'. At the moment, for the simulation result, 'sf' can only be '00' and the func returns the first 32 elements of v.

In [10]:
def reduced(v, sf):
    s=int(sf[0])
    f=int(sf[1])
    out=s*2+f
    res=[]
    for i in range(v.shape[0]):
        if((i>>5)==out):#((i%4)==out):#
            res.append(v[i])
    res=np.array(res)
    res=res/np.sqrt(np.sum(np.power(np.abs(res),2)))
    return np.array(res)

In [11]:
def msmtErrorMitFilter(backend, measured_qubit_list):
    # backend is the backend from which we obtain measurement error rates
    #measured_qubit_list contains
    qr = QuantumRegister(len(measured_qubit_list))
    qubit_list = range(len(measured_qubit_list))
    
    # Create the measurement calibration circuits
    meas_calibs, state_labels = complete_meas_cal(qubit_list=qubit_list, qr=qr, circlabel='mcal')
    
    # Create a noise model with the qubits being measured
    noise_model = noise.NoiseModel()
    back_prop = backend.properties()
    for qi in range(len(measured_qubit_list)):
        m0_p1 = back_prop.qubit_property(qi,name='prob_meas0_prep1')[0]
        m1_p0 = back_prop.qubit_property(qi,name='prob_meas1_prep0')[0]
        read_err = noise.errors.readout_error.ReadoutError([[1-m1_p0, m1_p0],[m0_p1,1-m0_p1]])
        noise_model.add_readout_error(read_err, [qi])
    
    # Execute the calibration circuits
    job = execute(meas_calibs, backend=backend_sim_local, shots=1000, noise_model=noise_model)
    cal_results = job.result()
    
    # Calculate the calibration matrix with the noise model
    meas_fitter = CompleteMeasFitter(cal_results, state_labels, qubit_list=qubit_list, circlabel='mcal')

    # Get the filter object
    meas_filter = meas_fitter.filter
    
    return meas_filter

In [12]:
def msmtErrorMitOnTom(results, meas_filter):
    #returns a dict of the form: {"('X','X','X','X','X')":[0001111:24, 1100011:445, ...], "(X','X','X','X','Y')":}
    mitigated_result = {}

    for data_idx, _ in enumerate(results.results):
        #     print(_.to_dict()['header']['name'])
        old_counts = results.get_counts(data_idx)
        new_counts = {}

        #     print(old_counts)
        # removes key structure
        for reg_key in old_counts:
            reg_bits = reg_key.split(' ')
            reg_bits = reg_bits[0]+reg_bits[1]
            new_counts[reg_bits]=old_counts[reg_key]

        # applies measurement filter
        #     print(new_counts)
        new_counts1 = meas_filter.apply(new_counts)
        mitigated_result[_.to_dict()['header']['name']] = new_counts1 
    return mitigated_result

In [13]:
def sort_list(list1, list2): 
    # sorts list 1 based on the sort indices of list 2
    zipped_pairs = zip(list2, list1) 
    z = [x for _, x in sorted(zipped_pairs)] 
      
    return z 

In [14]:
def extractMsmtQubits(circuit):

    # 'circuit' is the circuit for which we extract the list of measurement qubits
    # This is some messy code. Not sure if we necessarily have to parse the qasm file of a circuit to find the qubits being measured
    # Doesn't work too well when there are two classical registers. I've written up a fix but not happy with it.
    qasm_obj = circuit.qasm()
    t = qasm_obj.find("measure")
    qasm_obj = qasm_obj[t:-1]
    qasm_obj = qasm_obj.split(' ')
    listmsmt = []
    listclass = []
    for _ in qasm_obj:
        if 'q' in _:
            number = []
            for j in range(len(_)):
                if _[j] =='[':
                    temp1 = _[j+1:j+3].strip(']')
            listmsmt.append(int(temp1))
    for _ in qasm_obj:
        if 'c' in _:
            number = []
            for j in range(len(_)):
                if _[j] =='[':
                    temp1 = _[j+1:j+3].strip(']')
            if temp1 == '0' and len(listclass) > 4:
                temp1 = '5'
            if temp1 == '1' and len(listclass) > 4:
                temp1 = '6'
            listclass.append(int(temp1))
    listmsmt = sort_list(listmsmt, listclass)
#     print(listmsmt)
#     print(listclass)
    return listmsmt

In [32]:
def ddsSequence(qr, qc, target_qubit, backend):
    # qr = QuantumRegister, qc = QuantumCircuit, 
    # target_qubit = qubit on whcih DDS sequence is applied
    # backend = backend from which id gate time is extracted for required qubit.
    
    # Function creates a dds circuit whcih can be appended onto the existing circuit.
    
    id_gate_time = backend.properties().gate_length('id', target_qubit)
    
    # We might need to change the duration based on how long the qubit is idle.
    quadratic_sequence = new_predefined_dds(
    scheme='quadratic',
    duration=20e-6, 
    number_inner_offsets=2,
    number_outer_offsets=2,
    pre_post_rotation=True,
    name='Quadratic sequence')
    
    dds_circuit = convert_dds_to_qiskit_quantum_circuit(
    dynamic_decoupling_sequence=quadratic_sequence,
    target_qubits=target_qubit,
    gate_time=id_gate_time,
    add_measurement=False,
    )
        
    return dds_circuit

In [33]:
# TESTING
# target_qubit = 2
# backend.properties()._gates['id'][(target_qubit,)]['gate_length']
# backend.properties().gate_length('id', target_qubit)

qr = QuantumRegister(5)
qc = QuantumCircuit(qr)
target_qubit = 3

dds_circuit = ddsSequence(qr, qc, [target_qubit], backend)
dds_circuit.draw()

C:\Users\Prithviraj Prabhu\.conda\envs\qiskit2\lib\site-packages\qiskit\util.py:109: DeprecationWarning: The QuantumCircuit.iden() method is deprecated as of 0.14.0, and will be removed no earlier than 3 months after that release date. You should use the QuantumCircuit.i() method instead.
  return func(*args, **kwargs)
C:\Users\Prithviraj Prabhu\.conda\envs\qiskit2\lib\site-packages\qiskit\util.py:109: DeprecationWarning: The QuantumCircuit.iden() method is deprecated as of 0.14.0, and will be removed no earlier than 3 months after that release date. You should use the QuantumCircuit.i() method instead.
  return func(*args, **kwargs)
C:\Users\Prithviraj Prabhu\.conda\envs\qiskit2\lib\site-packages\qiskit\util.py:109: DeprecationWarning: The QuantumCircuit.iden() method is deprecated as of 0.14.0, and will be removed no earlier than 3 months after that release date. You should use the QuantumCircuit.i() method instead.
  return func(*args, **kwargs)
C:\Users\Prithviraj Prabhu\.conda\env

»
q5_0: ───────────────────────────────────────────────────────────────────────»
                                                                             »
q5_1: ───────────────────────────────────────────────────────────────────────»
                                                                             »
q5_2: ───────────────────────────────────────────────────────────────────────»
      ┌─────────────────────┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐»
q5_3: ┤ U3(pi/2,-pi/2,pi/2) ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├»
      └─────────────────────┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘»
«                                                                              »
«q5_0: ────────────────────────────────────────────────────────────────────────»
«                                                                              »
«q5_1: ────────────────────────────────────────────────────────────────────────»
«                                                                              »
«q5_2: ────────────────────────────────────────────────────────────────────────»
«       ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐»
«q5_3: ─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├»
«       ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘»
«                                                                         »
«q5_0: ───────────────────────────────────────────────────────────────────»
«                                                                         »
«q5_1: ───────────────────────────────────────────────────────────────────»
«                                                                         »
«q5_2: ───────────────────────────────────────────────────────────────────»
«       ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ »
«q5_3: ─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─»
«       ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ »
«                                                                           »
«q5_0: ─────────────────────────────────────────────────────────────────────»
«                                                                           »
«q5_1: ─────────────────────────────────────────────────────────────────────»
«                                                                           »
«q5_2: ─────────────────────────────────────────────────────────────────────»
«      ┌────────┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ »
«q5_3: ┤ U1(pi) ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─»
«      └────────┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ »
«                                                                              »
«q5_0: ────────────────────────────────────────────────────────────────────────»
«                                                                              »
«q5_1: ────────────────────────────────────────────────────────────────────────»
«                                                                              »
«q5_2: ────────────────────────────────────────────────────────────────────────»
«      ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ »
«q5_3: ┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─┤ I ├─░─»
«      └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ └───┘ ░ »
«                                                                              »
«q5_0: ────────────────────────────────────────────────────────────────────────»
«                                                                              »
«q5_1: ────────────────────────────────────────────────────────────────────────»
«                                                                              »
«q5_2: ────────────────────────────────────────────────────────────────────────»
«      ┌───┐ ░ ┌───┐ ░ ┌───┐ ░ ┌───┐

## Main part

Circuit | Description 
---| ---
qc0 | As shown in [6], state prepartion + stabilizer, no measurement
qc1 | add measurements on syndrome and flag qubits
qctom | add measurements on syndrome and flag qubits, then do state tomography on data qubits, used for tomography by both simulation and experiment
qctom_no_anc | qctom without measurement, used for 'tom.stateTomographyFitter'


In [49]:
def executeStatePreparation(stabilizer=0):
    #state vector
    q0, qc0=StatePreparation(stabilizer)
    qc0.draw()
    
    qc1=deepcopy(qc0)
    ca1 = ClassicalRegister(2)
    qc1.add_register(ca1)
    qc1.measure([q0[5],q0[6]],[ca1[0],ca1[1]])
    job = execute(qc1, backend_sv)
    psi_qc = job.result().get_statevector(qc1)
    
    #qasm simulation
    qctom = tom.state_tomography_circuits(qc0, data_list, meas_labels='Pauli', meas_basis='Pauli')
    qctom_no_anc = deepcopy(qctom)
    for qc in qctom:
        ca = ClassicalRegister(2)
        qc.add_register(ca)
        qc.measure([q0[5],q0[6]],[ca[0],ca[1]])
        
    # Create a noise model with the qubits being measured ------
    # ------used for testing measurement error mitigation on the simulator
    noise_model = noise.NoiseModel()
    back_prop = backend.properties()
    measured_qubit_list = extractMsmtQubits(qctom[-1])
    for qi in range(len(measured_qubit_list)):
        m0_p1 = back_prop.qubit_property(qi,name='prob_meas0_prep1')[0]
        m1_p0 = back_prop.qubit_property(qi,name='prob_meas1_prep0')[0]
        read_err = noise.errors.readout_error.ReadoutError([[1-m1_p0, m1_p0],[m0_p1,1-m0_p1]])
#         read_err = noise.errors.readout_error.ReadoutError([[0.7,0.3],[0.2,0.8]])
        noise_model.add_readout_error(read_err, [qi])
    
    job = execute(qctom, backend=backend_sim, optimization_level=0, shots=4096, noise_model=noise_model)
    results_sim=job.result()
#     print(results_sim)
    

    # Create an error mitigation filter ------
    # ------used for testing measurement error mitigation on the simulator
    measured_qubit_list = extractMsmtQubits(qctom[-1]) # assuming all the tomo circuits are identical except for basis changes
#     print(measured_qubit_list)
    filt = msmtErrorMitFilter(backend, measured_qubit_list)
    # Perform error mitigation on all the results
    results_sim_MM = msmtErrorMitOnTom(results_sim, filt)
    results_sim = results_sim_MM # this will be in the form: {"('X','X','X','X','X')":[0001111:24, 1100011:445, ...], "(X','X','X','X','Y')":}
    print(results_sim)
    
#     strip the registers for syndrome and flag extraction  
    result_sf={}
    for sf in ['00','01','10','11']:
            #outcomes: 00,01,10,11
            new_result = deepcopy(results_sim)

            for resultidx in results_sim.keys():
                old_counts = results_sim[resultidx]
                new_counts = {}

#                 #change the size of the classical register
#                 new_result.results[resultidx].header.creg_sizes = [new_result.results[resultidx].header.creg_sizes[0]]
#                 new_result.results[resultidx].header.clbit_labels = new_result.results[resultidx].header.clbit_labels[0:-2]
#                 new_result.results[resultidx].header.memory_slots = 5

                for reg_key in old_counts:
                    reg_bits = []
                    reg_bits.append(reg_key[0:2])
                    reg_bits.append(reg_key[2:7])
                    if (reg_bits[0]==sf):#reg_key is in the form like '00 10011', reg_bts[0]='00'
                        new_counts[reg_bits[1]]=old_counts[reg_key]
#                     print(type(reg_key))
#                     reg_bits = reg_key.split()
#                     if (reg_bits[0]==sf):#reg_key is in the form like '00 10011', reg_bts[0]='00'
#                         new_counts[reg_bits[1]]=old_counts[reg_key]

#                 new_result.results[resultidx].data.counts = \
#                     new_result.results[resultidx]. \
#                     data.counts.from_dict(new_counts)

                new_result[resultidx] = new_counts

                result_sf[sf]=new_result
    
    #test ----- cannot deepcopy results objects which have had some properties changed, as in above code
#     result_sf_dummy = deepcopy(result_sf['00'])
    
    #send the results to the state tomography filter
    
    tomo_qc_sim={}
#     for sf in ['00','01','10','11']:
#         tomo_qc_sim_sf = tom.StateTomographyFitter(result_sf[sf], qctom_no_anc, meas_basis='Pauli')
#         tomo_qc_sim[sf]=tomo_qc_sim_sf
    
#     max_job_count = 5
#     max_exp_per_job = 54
    
#     """ already created
#     qctom = tom.state_tomography_circuits(qc0, data_list, meas_labels='Pauli', meas_basis='Pauli')
#     for qc in qctom:
#         ca = ClassicalRegister(2)
#         qc.add_register(ca)
#         qc.measure([5,6],[5,6])
#     """
#     qctom = transpile(qctom, backend=backend)
    
#     #results_real=[]
#     #tomo_qc_real=[]
    
#     job_manager = IBMQJobManager()
#     start_time = time.time()
#     #for qc in qctom:
#     job_set_foo = job_manager.run(qctom, backend=backend, name='qctom', shots=2048, max_experiments_per_job=54)
#     job_status = job_set_foo.statuses()
#     while job_status[max_job_count-1] not in JOB_FINAL_STATES:
#         print(f'Status @ {time.time()-start_time:0.0f} s: {job_status[max_job_count-1]},'
#               f' ')
#         time.sleep(10)
#         job_status = job_set_foo.statuses()

#     results_real = job_set_foo.results()   
    
#     # Create an error mitigation filter
#     measured_qubit_list = extractMsmtQubits(qctom[-1]) # assuming all the tomo circuits are identical except for basis changes
#     filt = msmtErrorMitFilter(backend, measured_qubit_list)
#     # Perform error mitigation on all the results
#     results_real_MM = msmtErrorMitOnTom(results_real, filt)
    
#     tomo_qc_real = tom.StateTomographyFitter(results_real_MM, qctom, meas_basis='Pauli')
    #results_real.append(results_0)
    #tomo_qc_real.append(tomo_qc)
    results_real_MM = tomo_qc_real = []
    job_set_foo = 0
    return (psi_qc, results_sim, result_sf, tomo_qc_sim, job_set_foo, results_real_MM, tomo_qc_real)

In [50]:
dict={}
for i in range(1):
    data = executeStatePreparation(i)
    dict[i]=data
    #pickle.dump(data, open("Stabilizer%d"%i, "wb"))


{"('X', 'X', 'X', 'X', 'X')": {'0000000': 2.3490635220231835, '0000001': 265.0937437284836, '0000010': 231.05690592508878, '0000011': 3.8558901119137023, '0000100': 278.46174279350066, '0000101': 2.265171417408576, '0000110': 21.25592817533052, '0000111': 266.74910841547273, '0001000': 232.93882598225645, '0001001': 1.5992358784087338e-11, '0001010': 1.3041980116288023, '0001011': 285.03378264603083, '0001100': 1.8166948997119618e-12, '0001101': 270.83584803344496, '0001110': 235.8828849737312, '0001111': 3.583738966991665, '0010000': 244.50139537378664, '0010001': 2.8065009149224847, '0010010': 18.446181531028188, '0010011': 209.96851640997505, '0010100': 4.839867805878399e-12, '0010101': 281.37214694330476, '0010110': 228.85918117296794, '0010111': 2.8496944836484584e-12, '0011000': 6.189576089452107e-12, '0011001': 254.0342606977646, '0011010': 222.36583776561673, '0011011': 4.411156015011683e-12, '0011100': 256.5627303884309, '0011101': 16.464366436888596, '0011110': 1.852852162097

### Analyze the first stabilizer's result

In [51]:
psi_qc0, results_sim0, result_sf0, tomo_qc_sim0, job_set_foo0, results_real0, tomo_qc_real0=dict[0]

In [52]:
result_sf0

{'00': {"('X', 'X', 'X', 'X', 'X')": {'00000': 2.3490635220231835,
   '00001': 265.0937437284836,
   '00010': 231.05690592508878,
   '00011': 3.8558901119137023,
   '00100': 278.46174279350066,
   '00101': 2.265171417408576,
   '00110': 21.25592817533052,
   '00111': 266.74910841547273,
   '01000': 232.93882598225645,
   '01001': 1.5992358784087338e-11,
   '01010': 1.3041980116288023,
   '01011': 285.03378264603083,
   '01100': 1.8166948997119618e-12,
   '01101': 270.83584803344496,
   '01110': 235.8828849737312,
   '01111': 3.583738966991665,
   '10000': 244.50139537378664,
   '10001': 2.8065009149224847,
   '10010': 18.446181531028188,
   '10011': 209.96851640997505,
   '10100': 4.839867805878399e-12,
   '10101': 281.37214694330476,
   '10110': 228.85918117296794,
   '10111': 2.8496944836484584e-12,
   '11000': 6.189576089452107e-12,
   '11001': 254.0342606977646,
   '11010': 222.36583776561673,
   '11011': 4.411156015011683e-12,
   '11100': 256.5627303884309,
   '11101': 16.46436643

In [105]:
# print(results_sim0.to_dict())
# print(result_sf0)
dummy = result_sf0['00'].dict()
# dummy = results_sim0.to_dict()
dimmy = deepcopy(dummy)

for idx, _ in enumerate(dimmy['results']):
    if (idx == 0):
        temp = _['data']['counts'] 
        print(temp)
#         print(type(temp))
        newcs = {}
        for idxx, j in enumerate(temp):
            print(type(j))
            k = str(hex(int(j,2)))
            newcs[k] = temp[j]
        _['data']['counts'] = newcs
        temp = _['data']['counts'] 
        print(temp)
print(dimmy)
res = Result.from_dict(dimmy)
# print(dimmy)
print(res)

{'0111010': 1.28229462980482e-12, '0100001': 4.206981564903849, '1010011': 2.553180706965399e-11, '0110110': 6.148322607781273e-13, '0001011': 244.1426789359314, '0011111': 217.85322362784106, '0100000': 1.5876238703698552e-11, '1000000': 1.655769446736303e-11, '0011100': 258.52353777711653, '1000110': 5.253763766267456e-12, '1000101': 1.7737533553069892e-12, '1110110': 1.174956661527179e-12, '0010011': 279.5670563129508, '1110100': 2.5822265376368693e-13, '1010110': 1.6903082615336717e-11, '1010100': 8.5014509316801e-12, '0110001': 1.0370631284808469e-11, '0111101': 7.523297494560635e-12, '0010101': 279.7549125798886, '0001101': 245.37263741988042, '0010111': 8.371876118307769e-11, '0011010': 245.60981580856114, '1000111': 1.0299752284440466e-11, '0111100': 2.0285597867977835e-11, '0101001': 5.6920719402032564e-12, '1100000': 1.1656154869325305e-12, '1001101': 1.1036509884338718e-11, '0011101': 9.469704987608183e-12, '0000011': 7.541051797530093e-11, '0001001': 4.8614913113569274e-11,

ModelValidationError: "{'results': {1: {'data': {'counts': [{'0100001': ['String does not match expected pattern.'], '1010011': ['String does not match expected pattern.'], '0001011': ['String does not match expected pattern.'], '0011111': ['String does not match expected pattern.'], '1100101': ['String does not match expected pattern.'], '1000010': ['String does not match expected pattern.'], '1111101': ['String does not match expected pattern.'], '0011100': ['String does not match expected pattern.'], '1101001': ['String does not match expected pattern.'], '1000101': ['String does not match expected pattern.'], '0010011': ['String does not match expected pattern.'], '1110100': ['String does not match expected pattern.'], '1010100': ['String does not match expected pattern.'], '0110001': ['String does not match expected pattern.'], '1001010': ['String does not match expected pattern.'], '0111101': ['String does not match expected pattern.'], '0010101': ['String does not match expected

In [16]:
qcc, qc0=StatePreparation(0)
qc0.draw()
qc1=deepcopy(qc0)
ca1 = ClassicalRegister(2)
qc1.add_register(ca1)
qc1.measure([qcc[5],qcc[6]],[ca1[0],ca1[1]])
job0 = execute(qc1, backend_sv)

In [17]:
qctom = tom.state_tomography_circuits(qc0, data_list, meas_labels='Pauli', meas_basis='Pauli')
qctom_no_anc = deepcopy(qctom)

for qc in qctom:
    ca = ClassicalRegister(2)
    qc.add_register(ca)
    qc.measure([qcc[5],qcc[6]],[ca[0],ca[1]])

In [ ]:
qctom1 = tom.state_tomography_circuits(qc0, [0,1,2,3,4,5,6], meas_labels='Pauli', meas_basis='Pauli')

In [18]:
qctom[-1].draw()

┌───┐         ┌───┐                      ░  ░ ┌─┐                  
  q1_0: ┤ H ├─■─────■─┤ X ├──────────────────────░──░─┤M├──────────────────
        ├───┤ │     │ └─┬─┘                      ░  ░ └╥┘┌─┐               
  q1_1: ┤ H ├─■──■──┼───┼────────■───────────────░──░──╫─┤M├───────────────
        ├───┤    │  │   │        │               ░  ░  ║ └╥┘┌─┐            
  q1_2: ┤ H ├─■──■──┼───┼────────┼───────────────░──░──╫──╫─┤M├────────────
        ├───┤ │     │   │        │               ░  ░  ║  ║ └╥┘┌─┐         
  q1_3: ┤ H ├─■──■──┼───┼────────┼───────────────░──░──╫──╫──╫─┤M├─────────
        ├───┤    │  │   │        │               ░  ░  ║  ║  ║ └╥┘┌─┐      
  q1_4: ┤ H ├────■──■───┼────────┼───────■───────░──░──╫──╫──╫──╫─┤M├──────
        ├───┤           │        │       │ ┌───┐ ░  ░  ║  ║  ║  ║ └╥┘┌─┐   
  q1_5: ┤ H ├───────────■────■───■───■───■─┤ H ├─░──░──╫──╫──╫──╫──╫─┤M├───
        └───┘              ┌─┴─┐   ┌─┴─┐   └───┘ ░  ░  ║  ║  ║  ║  ║ └╥┘┌─┐
  q1_6: ───────────────────┤ X ├───┤ X ├─────────░──░──╫──╫──╫──╫──╫──╫─┤M├
                           └───┘   └───┘         ░  ░  ║  ║  ║  ║  ║  ║ └╥┘
  c1_0: ═══════════════════════════════════════════════╩══╬══╬══╬══╬══╬══╬═
                                                          ║  ║  ║  ║  ║  ║ 
  c1_1: ══════════════════════════════════════════════════╩══╬══╬══╬══╬══╬═
                                                             ║  ║  ║  ║  ║ 
  c1_2: ═════════════════════════════════════════════════════╩══╬══╬══╬══╬═
                                                                ║  ║  ║  ║ 
  c1_3: ════════════════════════════════════════════════════════╩══╬══╬══╬═
                                                                   ║  ║  ║ 
  c1_4: ═══════════════════════════════════════════════════════════╩══╬══╬═
                                                                      ║  ║ 
c244_0: ══════════════════════════════════════════════════════════════╩══╬═
                                                                         ║ 
c244_1: ═════════════════════════════════════════════════════════════════╩═

In [19]:
job = execute(qctom, backend=backend_sim, optimization_level=0, shots=4096)
results_sim=job.result()
print(results_sim)


Result(backend_name='ibmq_qasm_simulator', backend_version='0.4.1', date=datetime.datetime(2020, 5, 7, 20, 14, 37, 15562), header=Obj(backend_name='ibmq_qasm_simulator', backend_version='0.1.547'), job_id='5eb46c200e4b7c0011a405eb', metadata={'max_memory_mb': 257936, 'omp_enabled': True, 'parallel_experiments': 1, 'time_taken': 3.7558203260000003}, qobj_id='55067d1b-4c07-40f1-82fc-212544bcd6b3', results=[ExperimentResult(data=ExperimentResultData(counts=Obj(0x1=262, 0x10=275, 0x13=258, 0x15=266, 0x16=237, 0x19=241, 0x1a=254, 0x1c=268, 0x1f=242, 0x2=245, 0x4=271, 0x7=238, 0x8=258, 0xb=272, 0xd=267, 0xe=242)), header=Obj(clbit_labels=[['c1', 0], ['c1', 1], ['c1', 2], ['c1', 3], ['c1', 4], ['c2', 0], ['c2', 1]], creg_sizes=[['c1', 5], ['c2', 2]], memory_slots=7, n_qubits=7, name="('X', 'X', 'X', 'X', 'X')", qreg_sizes=[['q1', 7]], qubit_labels=[['q1', 0], ['q1', 1], ['q1', 2], ['q1', 3], ['q1', 4], ['q1', 5], ['q1', 6]]), meas_level=<MeasLevel.CLASSIFIED: 2>, metadata={'measure_sampling':

In [ ]:
# TESTING

measured_qubit_list = extractMsmtQubits(qctom[-1]) # assuming all the tomo circuits are identical except for basis changes
print(measured_qubit_list)
meas_filter = msmtErrorMitFilter(backend, measured_qubit_list)

In [38]:
# TESTING

results = results_sim
mitigated_result = {}

for data_idx, _ in enumerate(results.results):
#     print(_.name)
#     print(_.to_dict()['header']['name'])
    old_counts = results.get_counts(data_idx)
    new_counts = {}

#     print(old_counts)
    # removes key structure
    for reg_key in old_counts:
#             print(type(reg_key))
        reg_bits = reg_key.split(' ')
        reg_bits = reg_bits[0]+reg_bits[1]
        new_counts[reg_bits]=old_counts[reg_key]
                        
    # applies measurement filter
#     print(new_counts)
    new_counts1 = meas_filter.apply(new_counts)
    mitigated_result[_.to_dict()['header']['name']] = new_counts1 
    
#     print(new_counts1)
        
# #         #replaces key structure
# #         new_counts2 = {}
# #         for reg_key in new_counts1:
# # #             print(type(reg_key))
# #             reg_bits = []
# #             reg_bits.append(reg_key[0:2])
# #             reg_bits.append(reg_key[2:7])
# #             reg = reg_bits[0] + " " + reg_bits[1]
# #             new_counts2[reg]=new_counts1[reg_key]
# #         print(new_counts2)
    
#         mitigated_results.results[data_idx].data.counts = \
#             mitigated_results.results[data_idx]. \
#             data.counts.from_dict(new_counts1)

#         new_result.results[resultidx].data.counts = \
#                     new_result.results[resultidx]. \
#                     data.counts.from_dict(new_counts)
        
print(mitigated_result)






# # Create an error mitigation filter ------
# # ------used for testing measurement error mitigation on the simulator
# measured_qubit_list = extractMsmtQubits(qctom[-1]) # assuming all the tomo circuits are identical except for basis changes
# print(measured_qubit_list)
# filt = msmtErrorMitFilter(backend, measured_qubit_list)
# # Perform error mitigation on all the results
# results_sim_MM = msmtErrorMitOnTom(results_sim, filt)
# print(results_sim_MM)

{"('X', 'X', 'X', 'X', 'X')": {'0000001': 242.49992066863734, '0000010': 222.92117807394473, '0000100': 256.7193778972369, '0000111': 235.37789346411003, '0001000': 248.93964852905955, '0001011': 287.8434971354962, '0001101': 274.79900140523074, '0001110': 251.1022919762917, '0010000': 259.91628961772, '0010011': 257.134114559054, '0010101': 262.45821554384577, '0010110': 232.80976398012768, '0011001': 246.01411660427397, '0011010': 264.2434737842004, '0011100': 282.7636068916429, '0011111': 270.4576101424089, '0100111': 3.5973069727527003e-10, '0101011': 1.0444723254045478e-10, '0111001': 5.751652476934452e-11, '0111100': 1.4755422179102964e-10, '0111111': 3.2224636829123506e-10, '1000010': 2.666473734394447e-10, '1000100': 2.780886563558088e-10, '1000111': 3.150775582539812e-10, '1001000': 3.990221895026391e-10, '1001011': 1.6358988004316054e-10, '1001101': 3.4628762268771117e-10, '1001110': 4.836019994300003e-10, '1001111': 3.007081482607993e-10, '1010011': 3.6110582425605523e-10, '

In [ ]:
job_tmp=job_set_foo0.jobs()[0]

In [ ]:
jobs_tmp=job_set_foo0.jobs()[0]

In [ ]:
numresult=0
for i in range(len(job_set_foo0.jobs())):
    numresult+=len(job_set_foo0.jobs()[i].result().get_counts())
print(numresult)

In [ ]:
result_tmp=result_sf0['00']

### Strip the registers of syndrome and flag in results obtained from real qc
only '00' is kept

In [ ]:
numjobs=len(job_set_foo0.jobs())
#sf only consider 00
new_real_results=[]
for jobidx in range(numjobs):
    #job_set_foo0.jobs()[jobidx]
    numresults=len(job_set_foo0.jobs()[jobidx].result().results)
    new_result = deepcopy(job_set_foo0.jobs()[jobidx].result())
    for resultidx in range(numresults):
        #outcomes: 00,01,10,11

        old_counts=job_set_foo0.jobs()[jobidx].result().get_counts()[resultidx]
        new_counts={}
        new_result.results[resultidx].header.creg_sizes = [new_result.results[resultidx].header.creg_sizes[0]]
        new_result.results[resultidx].header.clbit_labels = new_result.results[resultidx].header.clbit_labels[0:-2]
        new_result.results[resultidx].header.memory_slots = 5

        for reg_key in old_counts:
            reg_bits = reg_key.split(' ')
            if (reg_bits[0]=='00'):#reg_key is in the form like '00 10011', reg_bts[0]='00'
                new_counts[reg_bits[1]]=old_counts[reg_key]

        new_result.results[resultidx].data.counts = \
            new_result.results[resultidx]. \
            data.counts.from_dict(new_counts)

    new_real_results.append(new_result)


Since there are multiple jobs, we need to combine the results with all kinds of Pauli measurements together

In [ ]:
new_real_results_sum=new_real_results[0]

In [ ]:
for i in range(len(new_real_results)-1):
    new_real_results_sum.results.extend(new_real_results[i+1].results)

Syndrome and flag are always 0 in the ideal simulation 

In [ ]:
rho_qc_sf0 = tomo_qc_sim0['11'].fit(method='lstsq')
# print(results_sim0)

In [ ]:
print(results_sim0)

fidelity between the reduced statevector of the circuit without measurement, and the reconstructed state of simulation tomography results

In [ ]:
F_qc_sf0 = state_fidelity(reduced(psi_qc0,'00'), rho_qc_sf0)
print(F_qc_sf0)

The following fidelity calculations are incorrect because noisy experimental results include those with non-zero syndrome or flag.

The fidelity between reconstruction using the simulation data and reconstruction using the real qc data

In [ ]:
tomo_qc_real00=tom.StateTomographyFitter(new_real_results_sum, qctom_no_anc, meas_basis='Pauli')

Show the difference between simulation & experiment outcomes with different Pauli bases...(not very accurate)

$\sum_{Pauli} (\sum_{i=00000}^{11111} |prob(i, simulation)-prob(i, experiment)|)$

$Pauli=(XXXXX, XXXXY, ..., ZZZZZ)$


In [ ]:
sum_diff=0
for key in tomo_qc_sim0['00'].data.keys():
    sum_sim=np.sum(list(tomo_qc_sim0['00'].data[key].values()))
    sum_real=np.sum(list(tomo_qc_real00.data[key].values()))
    diff=0
    for i in range(2**5):
        diff+=np.abs((tomo_qc_sim0['00'].data[key].get(bin(i)[2:],0)/sum_sim - tomo_qc_real00.data[key].get(bin(i)[2:],0)/sum_real))
    print(key, diff)
    sum_diff+=diff
print(sum_diff)

In [ ]:
tomo_qc_real00.data.values()

In [ ]:
tomo_qc_sim0['00'].data

In [ ]:
tomo_qc_real00.data

In [ ]:
from qiskit.visualization import *

In [ ]:
plot_histogram([tomo_qc_real00.data[('Z', 'Z', 'Z', 'Z', 'Z')],tomo_qc_sim0['00'].data[('Z', 'Z', 'Z', 'Z', 'Z')]])

In [ ]:
rho_real_sf00= tomo_qc_real00.fit(method='lstsq')

In [ ]:
np.linalg.norm(rho_real_sf00)

In [ ]:
F_qc_0=state_fidelity(rho_qc_sf0, rho_real_sf00)
print(F_qc_0)

Fidelity between the real-quantum-computer-data reconstruction and the ideal statevector

In [ ]:
F_qc_1=state_fidelity(reduced(psi_qc0,'00'), rho_real_sf00)
print(F_qc_1)

In [ ]:
test_allzero=np.zeros((32,32))
test_allzero[0][0]=1
F_qc_test=state_fidelity(reduced(psi_qc0, '00'),test_allzero)
print(F_qc_test)

In [ ]:
qctom_trans = transpile(qctom, backend=backend)

In [ ]:
for qc_trans in qctom_trans:
    print(qc_trans.depth())